# Multivariate LSTM Time Series Forecasting

In [150]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
from sklearn.preprocessing import LabelEncoder
from sklearn.preprocessing import MinMaxScaler
import warnings
warnings.filterwarnings('ignore')

In [151]:
df = pd.read_csv('covid_clean_imputted.csv')

In [152]:
df.head()

date state  critical_staffing_shortage_today_yes  \
0  2020-01-01    TX                                   0.0   
1  2020-01-01    HI                                   0.0   
2  2020-01-01    LA                                   0.0   
3  2020-01-01    NC                                   0.0   
4  2020-01-01    MN                                   0.0   

   critical_staffing_shortage_today_no  \
0                                  0.0   
1                                  0.0   
2                                  0.0   
3                                  0.0   
4                                  0.0   

   critical_staffing_shortage_today_not_reported  \
0                                            3.0   
1                                            1.0   
2                                            1.0   
3                                            1.0   
4                                            1.0   

   critical_staffing_shortage_anticipated_within_week_yes  \
0                                                0.0        
1                                                0.0        
2                                                0.0        
3                                                0.0        
4                                                0.0        

   critical_staffing_shortage_anticipated_within_week_no  \
0                                                0.0       
1                                                0.0       
2                                                0.0       
3                                                0.0       
4                                                0.0       

   critical_staffing_shortage_anticipated_within_week_not_reported  \
0                                                3.0                 
1                                                1.0                 
2                                                1.0                 
3                                                1.0                 
4                                                1.0                 

   hospital_onset_covid  inpatient_beds  ...  \
0                   0.0           790.0  ...   
1                   0.0             0.0  ...   
2                   0.0            41.2  ...   
3                   0.0            72.0  ...   
4                   0.0            46.0  ...   

   previous_day_admission_adult_covid_suspected_50-59  \
0                                                0.0    
1                                                0.0    
2                                                0.0    
3                                                0.0    
4                                                0.0    

   previous_day_admission_adult_covid_suspected_60-69  \
0                                                0.0    
1                                                0.0    
2                                                0.0    
3                                                0.0    
4                                                0.0    

   previous_day_admission_adult_covid_suspected_70-79  \
0                                                0.0    
1                                                0.0    
2                                                0.0    
3                                                0.0    
4                                                0.0    

   previous_day_admission_adult_covid_suspected_80+  \
0                                               0.0   
1                                               0.0   
2                                               0.0   
3                                               0.0   
4                                               0.0   

   previous_day_admission_adult_covid_suspected_unknown  deaths_covid  \
0                                                2.2              0.0   
1                                                2.2              0.0   
2                                                0.0       

In [153]:
# replace the row number with the date
df['date'] = pd.to_datetime(df['date'])
df = df.set_index('date')

In [154]:
#  sort the index by date in ascending order and then by country in descending order 
df = df.sort_index(ascending=True, axis=0)

# df = df.sort_index(ascending=True, axis=0)

In [155]:
# sort again by state
# df = df.sort_values(by=['state'])

In [156]:
df.head(5)

state  critical_staffing_shortage_today_yes  \
date                                                     
2020-01-01    TX                                   0.0   
2020-01-01    HI                                   0.0   
2020-01-01    LA                                   0.0   
2020-01-01    NC                                   0.0   
2020-01-01    MN                                   0.0   

            critical_staffing_shortage_today_no  \
date                                              
2020-01-01                                  0.0   
2020-01-01                                  0.0   
2020-01-01                                  0.0   
2020-01-01                                  0.0   
2020-01-01                                  0.0   

            critical_staffing_shortage_today_not_reported  \
date                                                        
2020-01-01                                            3.0   
2020-01-01                                            1.0   
2020-01-01                                            1.0   
2020-01-01                                            1.0   
2020-01-01                                            1.0   

            critical_staffing_shortage_anticipated_within_week_yes  \
date                                                                 
2020-01-01                                                0.0        
2020-01-01                                                0.0        
2020-01-01                                                0.0        
2020-01-01                                                0.0        
2020-01-01                                                0.0        

            critical_staffing_shortage_anticipated_within_week_no  \
date                                                                
2020-01-01                                                0.0       
2020-01-01                                                0.0       
2020-01-01                                                0.0       
2020-01-01                                                0.0       
2020-01-01                                                0.0       

            critical_staffing_shortage_anticipated_within_week_not_reported  \
date                                                                          
2020-01-01                                                3.0                 
2020-01-01                                                1.0                 
2020-01-01                                                1.0                 
2020-01-01                                                1.0                 
2020-01-01                                                1.0                 

            hospital_onset_covid  inpatient_beds  inpatient_beds_used  ...  \
date                                                                   ...   
2020-01-01                   0.0           790.0                 42.0  ...   
2020-01-01                   0.0             0.0                  0.0  ...   
2020-01-01                   0.0            41.2                 31.2  ...   
2020-01-01                   0.0            72.0                 53.2  ...   
2020-01-01                   0.0            46.0                 25.0  ...   

            previous_day_admission_adult_covid_suspected_50-59  \
date                                                             
2020-01-01                                                0.0    
2020-01-01                                                0.0    
2020-01-01                                                0.0    
2020-01-01                                                0.0    
2020-01-01                                                0.0    

            previous_day_admission_adult_covid_suspected_60-69  \
date                                                             
2020-01-01                                                0.0    
2020-01-01                                                0.0    
2020-01-01     

In [157]:
df.shape

(50088, 61)

## KPSS Test

In [158]:
from statsmodels.tsa.stattools import kpss
def kpss_test(series, **kw):    
    statistic, p_value, n_lags, critical_values = kpss(series, **kw)
    # Format Output
    print(f'KPSS Statistic: {statistic}')
    print(f'p-value: {p_value}')
    print(f'num lags: {n_lags}')
    print('Critial Values:')
    for key, value in critical_values.items():
        print(f'   {key} : {value}')
    print(f'Result: The series is {"not " if p_value < 0.05 else ""}stationary')

## Multivariate Time Series Forecasting with LSTMs in Keras

In [159]:
import plotly.express as px
import plotly.graph_objects as go
import plotly.io as pio
pio.templates.default = "plotly_white"

plot_template = dict(
    layout=go.Layout({
        "font_size": 18,
        "xaxis_title_font_size": 24,
        "yaxis_title_font_size": 24})
)

In [160]:
# plot the covid deaths sorted by month and grouped by state
fig = px.line(df, x=df.index, y='deaths_covid', color='state', title='Covid Deaths by State')
fig.update_layout(plot_template['layout'])
fig.show()

In [161]:
fig.update_yaxes(range = [0, 520])
fig.show()

## Create the target variable

In [162]:
# create a subset of the data for the state of California
df_ca = df[df['state'] == 'CA']

In [163]:
df = df_ca

In [164]:
#  drop state column
df = df.drop(['state'], axis=1)

In [165]:
target_sensor = "deaths_covid" # maybe specify a state ?
features = list(df.columns.difference([target_sensor]))

In [166]:
forecast_lead = 15
target = f"{target_sensor}_lead{forecast_lead}"

In [167]:
df[target] = df[target_sensor].shift(-forecast_lead)
df = df.iloc[:-forecast_lead]

## Create a hold-out test set and preprocess the data

In [168]:
# give the date index at 70% of the data
train_size = int(len(df) * 0.7)

In [169]:
# view row at index train_size
df.iloc[train_size]

critical_staffing_shortage_today_yes                       134.0
critical_staffing_shortage_today_no                        245.0
critical_staffing_shortage_today_not_reported               35.0
critical_staffing_shortage_anticipated_within_week_yes     152.0
critical_staffing_shortage_anticipated_within_week_no      227.0
                                                           ...  
all_pediatric_inpatient_bed_occupied                      3441.0
all_pediatric_inpatient_beds                              6138.0
staffed_pediatric_icu_bed_occupancy                       2213.0
total_staffed_pediatric_icu_beds                          3636.0
deaths_covid_lead15                                        157.0
Name: 2022-01-01 00:00:00, Length: 61, dtype: float64

In [170]:
test_start = "2022-01-01"

df_train = df.loc[:test_start].copy()
df_test = df.loc[test_start:].copy()

print("Test set fraction:", len(df_test) / len(df))

Test set fraction: 0.30093071354705275


## Standardize the features and target

In [171]:
target_mean = df_train[target].mean()
target_stdev = df_train[target].std()

for c in df_train.columns:
    mean = df_train[c].mean()
    stdev = df_train[c].std()

    df_train[c] = (df_train[c] - mean) / stdev
    df_test[c] = (df_test[c] - mean) / stdev

## Create datasets that PyTorch DataLoader can work with

In [172]:
import torch
from torch.utils.data import Dataset

class SequenceDataset(Dataset):
    def __init__(self, dataframe, target, features, sequence_length=5):
        self.features = features
        self.target = target
        self.sequence_length = sequence_length
        self.y = torch.tensor(dataframe[target].values).float()
        self.X = torch.tensor(dataframe[features].values).float()

    def __len__(self):
        return self.X.shape[0]

    def __getitem__(self, i): 
        if i >= self.sequence_length - 1:
            i_start = i - self.sequence_length + 1
            x = self.X[i_start:(i + 1), :]
        else:
            padding = self.X[0].repeat(self.sequence_length - i - 1, 1)
            x = self.X[0:(i + 1), :]
            x = torch.cat((padding, x), 0)

        return x, self.y[i]

In [173]:
i = 27
sequence_length = 8

train_dataset = SequenceDataset(
    df_train,
    target=target,
    features=features,
    sequence_length=sequence_length
)

X, y = train_dataset[i]
print(X)

tensor([[-1.3973, -3.4041, -1.1388, -3.9315, -3.3645, -2.9789, -2.3913, -2.4884,
         -1.8347, -0.6551, -1.6172, -1.8465, -0.6490, -1.5293, -1.3001, -1.0229,
         -3.7422, -1.1166, -3.7541, -3.3902, -1.1628, -0.9203, -3.6602, -3.3647,
         -1.0853, -3.4041, -1.1151, -1.0604, -1.1704, -1.3827, -1.3145, -1.2002,
         -1.0905, -0.9838, -0.9126, -0.8411, -0.4656, -2.5365, -1.4864, -2.4555,
         -2.5379, -2.1657, -2.3112, -2.3130, -2.3034, -2.1949, -0.2877, -1.0638,
         -1.6130, -2.9892, -1.1478, -1.1003, -1.9246, -0.9507, -0.8841, -1.6463,
         -1.4220, -3.3929, -2.0383],
        [-1.3973, -3.4041, -1.1388, -4.1988, -3.3645, -2.9790, -2.3913, -2.4884,
         -1.8347, -0.6551, -1.6172, -1.8465, -0.6490, -1.5293, -1.3001, -0.9428,
         -3.7406, -1.1162, -3.7526, -3.3876, -1.1623, -0.3075, -3.6587, -3.3622,
         -1.0155, -3.4016, -1.1146, -1.0558, -1.1704, -1.3827, -1.3145, -1.2002,
         -1.0905, -0.9838, -0.9126, -0.8411, -0.4656, -2.4972, -1.4864, 

In [174]:
X, y = train_dataset[i + 1]
print(X)

tensor([[-1.3973, -3.4041, -1.1388, -4.1988, -3.3645, -2.9790, -2.3913, -2.4884,
         -1.8347, -0.6551, -1.6172, -1.8465, -0.6490, -1.5293, -1.3001, -0.9428,
         -3.7406, -1.1162, -3.7526, -3.3876, -1.1623, -0.3075, -3.6587, -3.3622,
         -1.0155, -3.4016, -1.1146, -1.0558, -1.1704, -1.3827, -1.3145, -1.2002,
         -1.0905, -0.9838, -0.9126, -0.8411, -0.4656, -2.4972, -1.4864, -2.4555,
         -2.5379, -2.1657, -2.3112, -2.3130, -2.3034, -2.1949, -0.2877, -1.2786,
         -2.2924, -2.9893, -1.1476, -1.1001, -1.9246, -0.9507, -0.8841, -1.6463,
         -1.4220, -3.3929, -2.0383],
        [-0.7804, -3.3754, -1.1344, -1.6650, -3.3333, -2.9597, -2.3925, -2.4807,
         -1.8347, -0.6474, -1.6172, -1.8465, -0.6414, -1.5293, -1.3001, -0.8971,
         -3.7090, -1.1135, -3.7212, -3.3665, -1.1597, -1.2048, -3.6279, -3.3411,
         -0.9024, -3.3801, -1.1120, -1.0534, -1.1704, -1.3746, -1.3044, -1.1964,
         -1.0905, -0.9732, -0.9011, -0.8256, -0.4656, -2.5414, -1.4864, 

In [175]:
print(df_train[features].iloc[(i - sequence_length + 1): (i + 1)])

            adult_icu_bed_covid_utilization  \
date                                          
2020-03-16                        -1.397325   
2020-03-17                        -1.397325   
2020-03-18                        -0.780436   
2020-03-19                        -1.271226   
2020-03-20                        -1.193861   
2020-03-21                        -1.034247   
2020-03-22                        -1.034247   
2020-03-23                        -0.847619   

            adult_icu_bed_covid_utilization_denominator  \
date                                                      
2020-03-16                                    -3.404097   
2020-03-17                                    -3.404097   
2020-03-18                                    -3.375398   
2020-03-19                                    -3.374768   
2020-03-20                                    -3.375188   
2020-03-21                                    -3.375398   
2020-03-22                                    -3.375398  

In [176]:
from torch.utils.data import DataLoader
torch.manual_seed(99)

train_loader = DataLoader(train_dataset, batch_size=3, shuffle=True)

X, y = next(iter(train_loader))
print(X.shape)
print(X)

torch.Size([3, 8, 59])
tensor([[[-0.2024,  0.1158, -0.2104,  ...,  0.0029,  0.1134, -1.7716],
         [-0.2024,  0.1158, -0.2104,  ...,  0.0029,  0.1134, -1.7716],
         [-0.0676,  0.2104, -0.0762,  ...,  0.1444,  0.2050, -1.7672],
         ...,
         [-0.2024,  0.1158, -0.2104,  ...,  0.0029,  0.1134, -1.7716],
         [-0.1558,  0.1046, -0.1772,  ..., -0.0654,  0.1049, -1.7944],
         [-0.2024,  0.1158, -0.2104,  ...,  0.0029,  0.1134, -1.7716]],

        [[ 1.8433,  0.8178,  1.8800,  ...,  1.3350,  0.8281,  0.6340],
         [ 1.8220,  0.7931,  1.8426,  ...,  1.3594,  0.8041,  0.6091],
         [ 1.8104,  0.7490,  1.8007,  ...,  1.6522,  0.7613,  0.6099],
         ...,
         [ 1.4924,  0.7169,  1.4888,  ...,  1.5546,  0.7301,  0.5956],
         [ 1.4109,  0.7011,  1.4050,  ...,  1.3838,  0.7148,  0.6129],
         [ 1.3364,  0.6890,  1.3302,  ...,  1.2862,  0.7031,  0.6152]],

        [[-1.0836,  0.1387, -0.8935,  ..., -1.0804,  0.1320,  0.7464],
         [-1.0936,  0.

## Create the datasets and data loaders for real

In [189]:
torch.manual_seed(42)

batch_size = 64
sequence_length = 20

train_dataset = SequenceDataset(
    df_train,
    target=target,
    features=features,
    sequence_length=sequence_length
)
test_dataset = SequenceDataset(
    df_test,
    target=target,
    features=features,
    sequence_length=sequence_length
)

train_loader = DataLoader(train_dataset, batch_size=batch_size, shuffle=True)
test_loader = DataLoader(test_dataset, batch_size=batch_size, shuffle=False)

X, y = next(iter(train_loader))

print("Features shape:", X.shape)
print("Target shape:", y.shape)

Features shape: torch.Size([64, 20, 59])
Target shape: torch.Size([64])


## The model and learning algorithm

In [190]:
from torch import nn

class ShallowRegressionLSTM(nn.Module):
    def __init__(self, num_sensors, hidden_units):
        super().__init__()
        self.num_sensors = num_sensors  # this is the number of features
        self.hidden_units = hidden_units
        self.num_layers = 1

        self.lstm = nn.LSTM(
            input_size=num_sensors,
            hidden_size=hidden_units,
            batch_first=True,
            num_layers=self.num_layers
        )

        self.linear = nn.Linear(in_features=self.hidden_units, out_features=1)

    def forward(self, x):
        batch_size = x.shape[0]
        h0 = torch.zeros(self.num_layers, batch_size, self.hidden_units).requires_grad_()
        c0 = torch.zeros(self.num_layers, batch_size, self.hidden_units).requires_grad_()
        
        _, (hn, _) = self.lstm(x, (h0, c0))
        out = self.linear(hn[0]).flatten()  # First dim of Hn is num_layers, which is set to 1 above.

        return out

In [202]:
learning_rate = 1e-5
num_hidden_units = 16

model = ShallowRegressionLSTM(num_sensors=len(features), hidden_units=num_hidden_units)
loss_function = nn.MSELoss()
optimizer = torch.optim.Adam(model.parameters(), lr=learning_rate)

## Training

In [204]:
def train_model(data_loader, model, loss_function, optimizer):
    num_batches = len(data_loader)
    total_loss = 0
    model.train()
    
    for X, y in data_loader:
        output = model(X)
        loss = loss_function(output, y)

        optimizer.zero_grad()
        loss.backward()
        optimizer.step()

        total_loss += loss.item()

    avg_loss = total_loss / num_batches
    print(f"Train loss: {avg_loss}")

def test_model(data_loader, model, loss_function):
    
    num_batches = len(data_loader)
    total_loss = 0

    model.eval()
    with torch.no_grad():
        for X, y in data_loader:
            output = model(X)
            total_loss += loss_function(output, y).item()

    avg_loss = total_loss / num_batches
    print(f"Test loss: {avg_loss}")


print("Untrained test\n--------")
test_model(test_loader, model, loss_function)
print()

for ix_epoch in range(1000):
    print(f"Epoch {ix_epoch}\n---------")
    train_model(train_loader, model, loss_function, optimizer=optimizer)
    test_model(test_loader, model, loss_function)
    print()

Untrained test
--------
Test loss: 0.36733309626579286

Epoch 0
---------
Train loss: 0.7067707180976868
Test loss: 0.36756587624549864

Epoch 1
---------
Train loss: 0.7087610932913694
Test loss: 0.36781975626945496

Epoch 2
---------
Train loss: 0.689706412228671
Test loss: 0.36801367402076723

Epoch 3
---------
Train loss: 0.6707903282208876
Test loss: 0.3682392656803131

Epoch 4
---------
Train loss: 0.6757427941669117
Test loss: 0.3684718430042267

Epoch 5
---------
Train loss: 0.6952485767277804
Test loss: 0.36866583824157717

Epoch 6
---------
Train loss: 0.6751756234602495
Test loss: 0.3688942134380341

Epoch 7
---------
Train loss: 0.6714868355881084
Test loss: 0.36911354660987855

Epoch 8
---------
Train loss: 0.6779221594333649
Test loss: 0.36929606199264525

Epoch 9
---------
Train loss: 0.6877392814917997
Test loss: 0.36950318813323973

Epoch 10
---------
Train loss: 0.6612333492799238
Test loss: 0.36976189017295835

Epoch 11
---------
Train loss: 0.6709074879234488
Test l

## Evaluation

In [205]:
def predict(data_loader, model):

    output = torch.tensor([])
    model.eval()
    with torch.no_grad():
        for X, _ in data_loader:
            y_star = model(X)
            output = torch.cat((output, y_star), 0)
    
    return output


train_eval_loader = DataLoader(train_dataset, batch_size=batch_size, shuffle=False)

ystar_col = "Model forecast"
df_train[ystar_col] = predict(train_eval_loader, model).numpy()
df_test[ystar_col] = predict(test_loader, model).numpy()

df_out = pd.concat((df_train, df_test))[[target, ystar_col]]

for c in df_out.columns:
    df_out[c] = df_out[c] * target_stdev + target_mean

print(df_out)

            deaths_covid_lead15  Model forecast
date                                           
2020-02-04                  0.0        2.104858
2020-02-05                  0.0        2.104858
2020-02-06                  0.0        2.104858
2020-02-07                  0.0        2.104858
2020-02-08                  0.0        2.104858
...                         ...             ...
2022-10-14                  3.0       57.772842
2022-10-15                  3.0       64.394119
2022-10-16                  3.0       57.606808
2022-10-17                  3.0       60.013439
2022-10-18                  3.0       50.185986

[968 rows x 2 columns]


In [206]:
fig = px.line(df_out, labels=dict(created_at="Date", value="Covid Deaths in CA"))
fig.add_vline(x=test_start, line_width=4, line_dash="dash")
fig.add_annotation(xref="paper", x=0.75, yref="paper", y=0.8, text="Test set start", showarrow=False)
fig.update_layout(
    template=plot_template, legend=dict(orientation='h', y=1.02, title_text="")
)
fig.show()

In [207]:
#  calculate the mean absolute percentage error (MAPE)
def mape(y_true, y_pred):
    return np.mean(np.abs((y_true - y_pred) / y_true)) * 100

print("MAPE on train set:", mape(df_train[target], df_train[ystar_col]))
print("MAPE on test set:", mape(df_test[target], df_test[ystar_col]))

MAPE on train set: 143.1730927858003
MAPE on test set: 99.87657625582244


In [208]:
# calculate the mean absolute error (MAE)
def mae(y_true, y_pred):
    return np.mean(np.abs(y_true - y_pred))

print("MAE on train set:", mae(df_train[target], df_train[ystar_col]))
print("MAE on test set:", mae(df_test[target], df_test[ystar_col]))

MAE on train set: 0.17112374128254212
MAE on test set: 0.6296574312850269


In [209]:
# calculate the mean squared error (MSE)
def mse(y_true, y_pred):
    return np.mean(np.square(y_true - y_pred))

print("MSE on train set:", mse(df_train[target], df_train[ystar_col]))
print("MSE on test set:", mse(df_test[target], df_test[ystar_col]))

MSE on train set: 0.1159756735291799
MSE on test set: 0.4843423485281478


In [210]:
# calculate the root mean squared error (RMSE)
def rmse(y_true, y_pred):
    return np.sqrt(np.mean(np.square(y_true - y_pred)))

print("RMSE on train set:", rmse(df_train[target], df_train[ystar_col]))
print("RMSE on test set:", rmse(df_test[target], df_test[ystar_col]))

RMSE on train set: 0.34055201295716914
RMSE on test set: 0.6959470874485701
